## Final Project Submission

Please fill out:
* Student name: Stephan Osterburg
* Student pace: full time
* Scheduled project review date/time: 10/29/2018
* Instructor name: Rafael Carrasco 


### Import all needed libraries 

In [1]:
import os
import math
import random

import pandas as pd
import numpy as np
import json

from scipy import stats, linalg

import statsmodels.api as sm
import statsmodels.stats.stattools as sms
from statsmodels.formula.api import ols

from sklearn import linear_model
from sklearn import neighbors
from sklearn import preprocessing
from sklearn.metrics import mean_squared_error

import missingno as msno

import matplotlib.pyplot as plt
%matplotlib inline

import seaborn as sns
# set style
sns.set_style('whitegrid')
# overriding font size and line width
sns.set_context("notebook", font_scale=1.5, rc={"lines.linewidth": 2.5})

# map visualization
import folium

# don't print matching warnings
import warnings
warnings.filterwarnings('ignore') 


In [2]:
# import local functions
#
import functions as f

In [3]:
# you can check out the the documentation for the rest of the autoreaload modes
# by apending a question mark to %autoreload, like this:
# %autoreload?
#
%load_ext autoreload
%autoreload 2

#### Description of what can be found in the dataset

+ **ida** notation for a house
+ **date** Date house was sold
+ **price** Price is prediction target
+ **bedrooms** Number of Bedrooms/House
+ **bathrooms** Number of bathrooms/bedrooms
+ **sqft_living** square footage of the home
+ **sqft_lot** square footage of the lot
+ **floors** Total floors (levels) in house
+ **waterfront** House which has a view to a waterfront
+ **view** Has been viewed
+ **condition** How good the condition is ( Overall )
+ **grade** overall grade given to the housing unit, based on King County grading system
+ **sqft_above** square footage of house apart from basement
+ **sqft_basement** square footage of the basement
+ **yr_built** Built Year
+ **yr_renovated** Year when house was renovated
+ **zipcode** zip
+ **lat** Latitude coordinate
+ **long** Longitude coordinate
+ **sqft_living15** Living room area in 2015 (implies-- some renovations) This might or might not have affected the lot size area
+ **sqft_lot15** lotSize area in 2015 (implies-- some renovations)

# Questions:
1. Is location (zipcode/neighborhood) a indicator for house price? 
2. Does housing desity effect price?
3. Does the grade given reflect in the price?
4. Can we see if a house renovation reflects in the price?

## Obtaining Data

In [4]:
# read data and read date correctly
#
dataset = pd.read_csv("kc_house_data.csv", parse_dates = ['date'])

### Collecting basic informations about the data set

In [ ]:
dataset.shape

In [ ]:
dataset.dtypes

In [ ]:
dataset.isnull().sum()

### Get an initial big picture

___

# Scrubbing Data


## Cleaning Data

In [ ]:
# Display all missing data
#
msno.matrix(dataset)

In [ ]:
# Handling Null values for view
#
dataset.view.fillna(0, inplace=True)

In [ ]:
# Handling yr_renovated
# - create new column 'is_renovated' and 'yr_since_renovation'
# - if sqft_living15 > sqft_living set renovated
# - drop yr_renovated
#
import datetime
cur_year = datetime.datetime.now().year

def calc_years(row):
    return cur_year - row['yr_renovated'] if row['yr_renovated'] > 0 else 0

def set_renovated(row):
    return 1 if row['yr_since_renovation'] > 0 or row['sqft_living'] != row['sqft_living15'] else 0

# Set yr_renovated to int
dataset.yr_renovated.fillna(0, inplace = True)
# now I can convert yr_renovated to int
dataset.yr_renovated = dataset.yr_renovated.astype('int64')

dataset['yr_since_renovation'] = dataset.apply(calc_years, axis = 1)

# Create category 'is_renovated'
dataset['is_renovated'] = dataset.apply(set_renovated, axis=1)

dataset.drop(columns=['yr_renovated'], inplace=True)

In [ ]:
# While are at it, lets convert yr_built to house_age and drop yr_built
#
dataset['house_age'] = cur_year - dataset.yr_built
dataset.drop(columns=['yr_built'], inplace=True)

In [ ]:
# What is the percential of NaN in waterfront?
#
print(dataset.waterfront.isnull().sum() / dataset.shape[0])

In [ ]:
# Because the percential is about 10% we set the NaN values to zero
#
dataset.waterfront.fillna(0, inplace=True)

In [ ]:
msno.matrix(dataset)

In [ ]:
dataset.shape

### Cleaning basement feature

In [ ]:
# Handling sqft_basement
#
def calc_basement(row):
    """
    Calculate basement sqft based on difference sqft_living and sqft_above
    Deals at the same time with the '?'
    
    :param row: feature (column)
    :return: value (sqft)
    """
    return row['sqft_living'] - row['sqft_above'] if row['sqft_above'] < row['sqft_living']  else 0

dataset.sqft_basement = dataset.apply(calc_basement, axis = 1)

In [ ]:
# sort dataset by date and reset index (Do I have a good reason for it? No.)
#
dataset = dataset.sort_values(by = ['date'])
dataset = dataset.reset_index(drop=True)

### Get the big picture

In [ ]:
f.display_heatmap(dataset)

Initial observation:
    * In general there are very few strong correlations (around 0.7 and above)
    * price correlates to sqft_living (both), grade and very little to view
    * grade and sqft_above do correlate
    * we can consolidate sqft_living, sqft_living15 and sqft_above

**Question:** What of the following sqft columns matter most?
    + sqft_above
    + sqft_basement
    + sqft_living
    + sqft_living15
    + sqft_lot
    + sqft_lot15
    
*Note:* sqft_living15 and sqft_lot15 are baseed on 2015 input

___

## Visualize house prices and density by zipcode

Because it's a question want to try to answer, but it's not reflected in the above initial corr plot

In [5]:
# Set zipcode type to string (folium)
dataset['zipcode'] = dataset['zipcode'].astype('str')

# get the mean value across all data points
zipcode_data = dataset.groupby('zipcode').aggregate(np.mean)
zipcode_data.reset_index(inplace = True)

In [21]:
# count number of houses grouped by zipcode
#
dataset['count'] = 1
t = dataset.groupby('zipcode').sum()
t.reset_index(inplace = True)
t = t[['zipcode', 'count']]
zipcode_data = pd.merge(zipcode_data, t, on='zipcode')

# drop count from org dataset
dataset.drop(['count'], axis = 1, inplace = True)

zipcode_data.head(2)

zipcode          price  sqft_living15     mean_price  mean_sqft_living15  \
0   98001  281194.869806    1830.099723  281194.869806         1830.099723   
1   98002  234284.035176    1479.030151  234284.035176         1479.030151   

   count  
0    361  
1    199

In [24]:
# Get geo data file path
geo_data_file = os.path.join('data', 'king_county_wa_zipcode_area.geojson')

# load GeoJSON
with open(geo_data_file, 'r') as jsonFile:
    geo_data = json.load(jsonFile)
    
tmp = geo_data

# remove ZIP codes not in geo data
geozips = []
for i in range(len(tmp['features'])):
    if tmp['features'][i]['properties']['ZIPCODE'] in list(zipcode_data['zipcode'].unique()):
        geozips.append(tmp['features'][i])

# creating new JSON object
new_json = dict.fromkeys(['type','features'])
new_json['type'] = 'FeatureCollection'
new_json['features'] = geozips

# save uodated JSON object
open("cleaned_geodata.json", "w").write(json.dumps(new_json, sort_keys=True, indent=4, separators=(',', ': ')))

11783863

In [27]:
f.map_feature_by_zipcode(zipcode_data, 'count')

In [25]:
f.map_feature_by_zipcode(zipcode_data, 'price')

In [30]:
# Get the top 5 zipcode by price
#
zipcode_data.nlargest(5, 'price')

zipcode         price  sqft_living15    mean_price  mean_sqft_living15  \
24   98039  2.161300e+06    3132.200000  2.161300e+06         3132.200000   
3    98004  1.356524e+06    2674.700315  1.356524e+06         2674.700315   
25   98040  1.194874e+06    2898.744681  1.194874e+06         2898.744681   
48   98112  1.096239e+06    2280.078067  1.096239e+06         2280.078067   
41   98102  8.996077e+05    1954.471154  8.996077e+05         1954.471154   

    count  
24     50  
3     317  
25    282  
48    269  
41    104

___

### Categorize Data

In [ ]:
dataset['condition'] = dataset['condition'].astype('category', ordered = True)
dataset['waterfront'] = dataset['waterfront'].astype('category', ordered = True)
dataset['is_renovated'] = dataset['renovated'].astype('category', ordered = False)
dataset['view'] = dataset['view'].astype('category', ordered = False)
dataset['grade'] = dataset['grade'].astype('category', ordered = False)

# Create category 'has_basement'
dataset['has_basement'] = dataset.sqft_basement.apply(lambda x: 1 if x > 0 else 0)
dataset['has_basement'] = dataset.has_basement.astype('category', ordered = False)

In [ ]:
# dropping id and date
dataset.drop(['id', 'date'], axis = 1, inplace = True)

In [ ]:
# Set dummies
cat_columns = ['floors', 'view', 'grade', 'condition']

for col in cat_columns:
    dummies = pd.get_dummies(subset_df[col], drop_first=False)
    dummies = dummies.add_prefix("{}_".format(col))
    
    dataset.drop(col, axis=1, inplace=True)
    dataset = subset_df.join(dummies)

___

### Get a gerneral overview via scatter plot

In [ ]:
cols = ['price', 'bedrooms', 'bathrooms', 'sqft_above', 'sqft_basement', 'sqft_living15', 'floors', 
        'sqft_lot15', 'yr_since_renovation', 'yr_built', 'view', 'condition', 'grade', 'renovated']

In [ ]:
ncol = 3 # pick one dimension
nrow = math.floor((len(cols)+ ncol-1) / ncol) # make sure enough subplots
fig, axarr = plt.subplots(nrows=nrow, ncols=ncol, figsize=(20, 20)) # create the axes

for i in range(len(cols)): # go over a linear list of data
    ix = np.unravel_index(i, axarr.shape) # compute an appropriate index (1d or 2d)

    name = cols[i]
    dataset.plot(kind='scatter', x=name, y='price', ax=axarr[ix], label=name) 

plt.tight_layout()
plt.show();

**Notes:** 
    * lets have a closer look at sqft_living15 and price
    * do bedroom really effect price? (espially when one has 30+ of them)
    + how does age (yr_built) and sqft_living coerlate?

In [ ]:
ax = plt.figure(figsize=(16, 8))
ax = sns.kdeplot(dataset.price, dataset.sqft_living15, n_levels=30)

In [ ]:
ax = plt.figure(figsize=(16, 8))
ax = sns.kdeplot(dataset.price, dataset.yr_built, n_levels=30)

In [ ]:
ax = plt.figure(figsize=(16, 8))
ax = sns.kdeplot(dataset.sqft_living15, dataset.yr_built, n_levels=30)

___

##### Initial  
+ yr_renovated = float, should be int
+ categories:
    - waterfront (later)
    - renovated
    - condition
    - grade
+ create new categories (maybe): 
    - upscaled (0, 1)
    - downscaled (0, 1)
+ create new column:
    - yr_since_renovation (yr_renovated -> convert to "how long ago")
    - renovated (category)
+ to be removed:
    - sqft_above, sqft_basement
    - lat, long (might be useful later for viz work)
    - id, date
+ consolidate later:
    - sqft_living, sqft_living15
    - sqft_lot, sqft_lot15

### Normalizing Data

## Subset exploration

In [ ]:
# Create subset of dataset (10%)
#
subset_df = dataset.sample(frac=0.1)

In [ ]:
subset_df.shape

___

### Identifying Multicollinearity

In [ ]:
# Correlation Matrix
subset_df.corr()

In [ ]:
abs(subset_df.corr()) > 0.75

In [ ]:
# Checking if there might be some data loss  or so....
#
f.display_heatmap(subset_df)

___

## Regression Model

In [ ]:
ols_results = [['ind_var', 'r_squared', 'intercept', 'slope', 'p-value', 'normality (JB)']]

In [ ]:
def run_ols_regression(store_results, data, target, feature):
    """
    Run ols model, prints model summary, displays plot_regress_exog and qqplot
    
    :param data: dataset
    :param target: target feature name
    :param feature: feature name
    :return:
    """
    
    formula = target + '~' + feature
    model = ols(formula=formula, data=data).fit()
    
    print('Regression Analysis and Diagnostics for formula: ', formula)
    print('\n')

    df = pd.DataFrame({feature: [subset_df[feature].min(), subset_df[feature].max()]})
    pred = model.predict(df)

    fig = plt.figure(figsize=(16, 8))
    fig = sm.graphics.plot_regress_exog(model, feature, fig=fig)
    plt.show();

    residuals = model.resid
    fig = sm.graphics.qqplot(residuals, dist=stats.norm, line='45', fit=True)
    fig.show();
    
    # append all information to results
    store_results.append([feature, model.rsquared, model.params[0], model.params[0],
                        model.pvalues[1], sms.jarque_bera(model.resid)[0]])


In [ ]:
run_ols_regression(ols_results, subset_df, 'price', 'sqft_living15')

In [ ]:
pd.DataFrame(ols_results)

## Exploring Cleaning Outliers 

### 1. Winsorize features

In [ ]:
filt_df = subset_df[['price', 'sqft_living15']]

In [ ]:
def winsorize_features(df):
    """
    Returns a Winsorized version of the input array
    
    :param df: input dataset
    :return: skipped dataset
    """
    return stats.mstats.winsorize(df, limits=[0.05, 0.05])

In [ ]:
winsr_df = filt_df.transform(winsorize_features)

In [ ]:
winsr_df[['price', 'sqft_living15']].hist(figsize  = [6, 6]);

In [ ]:
winsr_results = [['ind_var', 'r_squared', 'intercept', 'slope', 'p-value', 'normality (JB)']]

In [ ]:
run_ols_regression(winsr_results, winsr_df, 'price', 'sqft_living15')

### 2. Normalizing features

In [ ]:
norm_df = subset_df[['price', 'sqft_living15', 'sqft_lot']]

In [ ]:
scaler = preprocessing.MinMaxScaler()
scaled_df = scaler.fit_transform(norm_df)
scaled_df = pd.DataFrame(scaled_df, columns=['price', 'sqft_living15', 'sqft_lot'])

In [ ]:
scaled_df[['price', 'sqft_living15']].hist(figsize  = [6, 6]);

In [ ]:
norm_results = [['ind_var', 'r_squared', 'intercept', 'slope', 'p-value', 'normality (JB)']]

In [ ]:
run_ols_regression(norm_results, scaled_df, 'price', 'sqft_living15')

In [ ]:
# Result from the unfiltered df
pd.DataFrame(ols_results)

In [ ]:
# Winsorized results
pd.DataFrame(winsr_results)

In [ ]:
# NOrmalized results
pd.DataFrame(norm_results)

In [ ]:
subset_df.columns

In [ ]:
X = scaled_df[['sqft_living15', 'sqft_lot']]
X_int = sm.add_constant(X)
y = pd.DataFrame(scaled_df, columns= ["price"])

model = sm.OLS(y, X_int).fit()
model.summary()

___

### Investigating Continuos Variables

In [ ]:
continous_vars = ['yr_built', 'sqft_basement', 'sqft_living15', 'sqft_lot', 'yr_since_renovation']

In [ ]:
f.display_jointplot(subset_df, continous_vars)

In [ ]:
f.measure_strength(subset_df, continous_vars, 'price')

In [ ]:
# Display bos-and-whisker plot showing as well outliers
#
f.display_plot(subset_df, continous_vars, 'price')

### Investigate Discrete Variables

In [ ]:
discrete_vars = ['grade', 'condition', 'view', 'floors', 'bedrooms', 'bathrooms']

In [ ]:
f.display_jointplot(dataset, discrete_vars)

In [ ]:
f.measure_strength(subset_df, discrete_vars, 'price')

In [ ]:
# Display bos-and-whisker plot showing as well outliers
#
f.display_plot(subset_df, discrete_vars, 'price')

### Relational plots

In [ ]:
g = sns.relplot(x="sqft_living15", y="price", hue="price", col="grade", 
                size="price", sizes=(5, 500), col_wrap=3, data=subset_df)

g

In [ ]:
g = sns.relplot(x="sqft_living15", y="price", hue="price", col="condition", 
                size="price", sizes=(5, 500), col_wrap=3, data=subset_df)

g

In [ ]:
g = sns.relplot(x="sqft_living15", y="price", hue="price", col="renovated", 
                size="price", sizes=(5, 500), col_wrap=3, data=subset_df)

g

#### Observation
+ grade and price have moderate high correlation
+ bathrooms and price have a moderate correlation
+ bedrooms, floors and view have a lower than moderate correlation to price
+ condition has none

## Basic visual of some data of interest

## Feature Scaling and Normalization